# import packages

In [1]:
import pandas as pd
import numpy as np
import json
import torch
from torch import nn
import math

# Evironment Setup

In [2]:
import os

seed = 42
np.random.seed(seed)
os.environ['PYTHONHASHSEED'] = str(seed)
torch.manual_seed(seed)
torch.cuda.manual_seed(seed)
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

device = "cuda" if torch.cuda.is_available() else "cpu"
device = "cuda:1"
print("Device: ", device)

# os.environ['CUDA_LAUNCH_BLOCKING'] = "1"
# os.environ['TORCH_USE_CUDA_DSA'] = "1"

EXP_NAME = 'BERT_pretraining_on_wiki'

Device:  cuda:1


In [3]:
# from google.colab import drive
# drive.mount('/content/drive')

In [4]:
# import os
# os.chdir('/content/drive/MyDrive/NLP')

# preprocess data

In [26]:
corpus[0]['input']

"The Kellys and the O'Kellys is a novel by Anthony Trollope."

In [5]:
with open('./data/wiki.json', 'r') as f:
    corpus = json.load(f)

In [6]:
len(corpus)

30000

In [7]:
print(corpus[0]['input'])
print(corpus[0]['label'])

The Kellys and the O'Kellys is a novel by Anthony Trollope.
It was written in Ireland and published in 1848..


In [29]:
corpus[0]['input'].count(" ")

10

In [28]:
max_len = 0
for data in corpus:
    len = data['input'].count(" ")+1
    if max_len < len:
        max_len = len
print(max_len)

7113


In [8]:
train_num = int(len(corpus) * 0.8)

corpus_train = corpus[:train_num]
corpus_test = corpus[train_num:]

In [9]:
train_input = ['SOS ' + sentence['input'] + ' EOS' for sentence in corpus_train]
train_label = ['SOS ' + sentence['label'] + ' EOS' for sentence in corpus_train]

tot_data = []

tot_data.extend(train_input)
tot_data.extend(train_label)

In [10]:
test_input = ['SOS ' + sentence['input'] + ' EOS' for sentence in corpus_test]
test_label = ['SOS ' + sentence['label'] + ' EOS' for sentence in corpus_test]

tot_data_test = []

tot_data_test.extend(test_input)
tot_data_test.extend(test_label)

In [11]:
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

# Initialize the tokenizer
tokenizer = Tokenizer(num_words=64825, oov_token="<OOV>")

# Fit the tokenizer on the texts
# tokenizer.fit_on_texts(dialogs)
tokenizer.fit_on_texts(tot_data + tot_data_test) # Changed

# Convert texts to sequences of integers
train_input = tokenizer.texts_to_sequences(train_input)
train_label = tokenizer.texts_to_sequences(train_label)

# Pad the sequences to have equal length
# patient_ques = pad_sequences(patient_ques, padding='post')
# docter_ans = pad_sequences(docter_ans, padding='post')

print("Word Index = " , tokenizer.word_index)
print("Sequences = " , train_input)
# print("Padded Sequences:")
# print(padded_sequences)

2023-12-07 11:20:55.827366: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-12-07 11:20:55.893134: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-07 11:20:55.893189: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-07 11:20:55.895085: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-07 11:20:55.905771: I tensorflow/core/platform/cpu_feature_guar

Word Index =  {'<OOV>': 1, 'the': 2, 'sos': 3, 'eos': 4, 'of': 5, 'in': 6, 'and': 7, 'a': 8, 'to': 9, 'is': 10, 'was': 11, 'as': 12, 'for': 13, 'by': 14, 'on': 15, 'it': 16, 'he': 17, 'with': 18, 'from': 19, 'at': 20, 'an': 21, 'his': 22, 'that': 23, 'are': 24, 'which': 25, 'also': 26, 'its': 27, 'has': 28, 'first': 29, 'or': 30, 'were': 31, 'one': 32, 'this': 33, 'after': 34, 'new': 35, 'who': 36, 'be': 37, 'born': 38, 'she': 39, '1': 40, 'two': 41, 'their': 42, 'american': 43, 'known': 44, 'national': 45, 'been': 46, '2': 47, 'had': 48, 'united': 49, 'film': 50, 'during': 51, 'have': 52, 'state': 53, 'but': 54, 'other': 55, 'they': 56, 'world': 57, 'south': 58, 'university': 59, 'states': 60, 'most': 61, 'part': 62, 'city': 63, 'her': 64, 'all': 65, 'district': 66, 'north': 67, 'not': 68, 'located': 69, 'into': 70, 'school': 71, 'county': 72, 'between': 73, 'may': 74, 'three': 75, 'time': 76, '–': 77, 'played': 78, 'season': 79, 'won': 80, 'album': 81, 'over': 82, 'when': 83, 'league

In [12]:
# Changed

test_input = tokenizer.texts_to_sequences(test_input)
test_label = tokenizer.texts_to_sequences(test_label)

print("Sequences = " , test_input)

Sequences =  [[3, 17, 11, 42597, 6, 1158, 4], [3, 725, 8602, 6536, 10, 349, 8, 1818, 5, 4075, 1398, 4], [3, 61262, 2435, 10, 8, 155, 14, 43, 3259, 139, 2, 6941, 61263, 4], [3, 658, 6, 742, 16, 791, 145, 216, 15, 2, 579, 674, 664, 145, 75, 15, 2, 381, 1299, 2457, 674, 664, 7, 145, 3142, 15, 2, 381, 920, 1299, 442, 4], [3, 61264, 10, 8, 22490, 158, 119, 6, 2, 49, 385, 4], [3, 2, 61265, 1097, 204, 6630, 296, 11, 2, 232, 2088, 1722, 5054, 705, 84, 6, 884, 19, 277, 9, 282, 4], [3, 2, 232, 204, 443, 19, 2, 45, 6630, 296, 2355, 13, 2, 356, 4], [3, 61266, 61267, 61268, 61269, 10, 8, 122, 6, 2, 696, 66, 5, 1421, 42598, 24428, 195, 42599, 72, 7832, 1525, 6, 120, 184, 681, 4], [3, 42600, 24, 18045, 9, 61270, 61271, 42601, 770, 61272, 61273, 61274, 30, 61275, 18, 61276, 6, 353, 1029, 54, 61277, 603, 108, 30, 1083, 61278, 30, 61279, 4], [3, 5058, 868, 38, 417, 176, 858, 10, 8, 850, 36, 78, 12, 8, 3635, 4], [3, 25721, 10, 21, 2211, 286, 6, 416, 72, 2477, 49, 60, 4], [3, 16, 10, 67, 5, 2, 25721, 245,

In [13]:
segmented_embedding = []
for sequence in train_input:
    segment_ids = []
    for token_id in sequence:
        segment_ids.append(1)
    segmented_embedding.append(segment_ids)

In [14]:
# Changed
segmented_embedding_test = []
for sequence in test_input:
    segment_ids = []
    for token_id in sequence:
        segment_ids.append(1)
    segmented_embedding_test.append(segment_ids)

# Initialize Dataloader

In [15]:
# Create train dataset and dataloader

from torch.utils.data import DataLoader
from src.Datasets import WikiDataset

batch_size = 32  # Define the batch size
train_input = torch.tensor(pad_sequences(train_input, padding='post'))
train_label = torch.tensor(pad_sequences(train_label, padding='post'))
train_seg_emb = torch.tensor(pad_sequences(segmented_embedding, padding='post'))

wiki_dataset = WikiDataset(train_input, train_label, train_seg_emb)
wiki_dataloader = DataLoader(wiki_dataset, batch_size=batch_size, shuffle=True)

In [16]:
# Create test dataset and dataloader # Changed
test_input = torch.tensor(pad_sequences(test_input, padding='post'))
test_label = torch.tensor(pad_sequences(test_label, padding='post'))
test_seg_emb = torch.tensor(pad_sequences(segmented_embedding_test, padding='post'))
wiki_dataset_test = WikiDataset(test_input, test_label, test_seg_emb)
wiki_dataloader_test = DataLoader(wiki_dataset_test, batch_size=batch_size, shuffle=False)

# Initialize BERT

In [17]:
# Initialize the model
 
from src.BERT import BERT

model = BERT(num_embeddings=len(tokenizer.word_index)+10).to(device)

for i, data in enumerate(wiki_dataloader):
    inputs = data['input'].to(device)
    labels = data['label'].to(device)
    segment_embeddings = data['segment_embedding'].to(device)
    break   # Changed

print(inputs.shape)
print(labels.shape)
print(segment_embeddings.shape)

output = model(inputs, segment_embeddings)[:,201:,:]

output.shape

torch.Size([32, 313])
torch.Size([32, 715])
torch.Size([32, 313])


torch.Size([32, 112, 64834])

# Define Loss and Optimizer

In [18]:
# Define loss function and optimizer

from torch.nn import CrossEntropyLoss
from torch.optim import AdamW

loss_function = CrossEntropyLoss(ignore_index=0)
optimizer = AdamW(model.parameters(), lr=0.001)


# Train

In [19]:
import torch
from tqdm import tqdm

min_loss = 1e9

# Training loop
num_epochs = 200
for epoch in range(num_epochs):  # num_epochs should be defined
    model.train()
    total_loss = 0
    total_loss_test = 0   # Changed

    # Progress Bar
    batch_bar   = tqdm(total=len(wiki_dataloader), dynamic_ncols=True, leave=False, position=0, desc='Train', ncols=5)

    for i, data in enumerate(wiki_dataloader):
        # Forward pass
        
        model.train()

        inputs = data['input'].to(device)
        labels = data['label'].to(device).long()
        segment_embeddings = data['segment_embedding'].to(device)

        # if(len(patient_questions)!=batch_size):
        #   print('jump')
        #   continue
        optimizer.zero_grad()
        output = model(inputs, segment_embeddings)


        # output = output[:, 201:, :] # Changed
        ans_seq_len = labels.shape[1]
        output = output[:, :ans_seq_len, :] # Changed
        # out_seq_len = output.shape[1]
        # labels = labels[:, :out_seq_len]
        # output = output.softmax(dim=-1)
        # Compute loss - ensure doctor_answers is the correct target and has the right shape

        loss = loss_function(output.reshape(-1, output.size(-1)), labels.reshape(-1))
        total_loss += loss.item()

        # Backward pass and optimization
        loss.backward()
        optimizer.step()

        batch_bar.set_postfix(
            loss        = "{:.04f}".format(float(total_loss / ((i+1) * wiki_dataloader.batch_size))),
        )

        batch_bar.update() # Update tqdm bar

    batch_bar.close()
    
    print(f"Epoch {epoch+1}/{num_epochs}, Train Loss: {total_loss/len(wiki_dataloader)}")

    # Progress Bar
    batch_bar   = tqdm(total=len(wiki_dataloader_test), dynamic_ncols=True, leave=False, position=0, desc='Test', ncols=5)

    # Changed
    with torch.no_grad():
        for i, data in enumerate(wiki_dataloader_test):
            # Forward pass
            
            model.eval()

            inputs = data['input'].to(device)
            labels = data['label'].to(device).long()
            segment_embeddings = data['segment_embedding'].to(device)

            output = model(inputs, segment_embeddings)

            ans_seq_len = labels.shape[1]
            output = output[:, :ans_seq_len, :] # Changed
            # # out_seq_len = output.shape[1]
            # # labels = labels[:, :out_seq_len]

            loss = loss_function(output.reshape(-1, output.size(-1)), labels.reshape(-1))
            total_loss_test += loss.item()

            batch_bar.set_postfix(
                loss        = "{:.04f}".format(float(total_loss / ((i+1) * wiki_dataloader_test.batch_size))),
            )

            batch_bar.update() # Update tqdm bar

    if loss < min_loss:
        min_loss = loss
        torch.save({
            'epoch': epoch,
            'model_state_dict': model.state_dict(),
            'optimizer_state_dict': optimizer.state_dict(),
            'loss': loss,
            }, os.path.join('experiments', EXP_NAME, 'best.pth'))

    if epoch % 10 == 0 or epoch == num_epochs-1:
            pred = torch.argmax(output, dim=-1)

            temp = [seq[:seq.index(0)] if seq.count(0) != 0 else seq for seq in inputs.cpu().tolist()]
            print("Input :", tokenizer.sequences_to_texts(temp)[:1])
            temp = [seq[:seq.index(0)] if seq.count(0) != 0 else seq for seq in labels.cpu().tolist()]
            print("Label :", tokenizer.sequences_to_texts(temp)[:1])
            temp = [seq[:seq.index(0)] if seq.count(0) != 0 else seq for seq in pred.cpu().tolist()]
            print("Predi :", tokenizer.sequences_to_texts(temp)[:1])
            print("Loss : ", loss_function(output[0].reshape(-1, output.size(-1)), labels[0].reshape(-1)))
    
            
    batch_bar.close()

    print(f"Epoch {epoch+1}/{num_epochs}, Test  Loss: {total_loss_test/len(wiki_dataloader_test)}")
    print("===============================================")


Train:   0%|          | 0/750 [00:00<?, ?it/s]

ValueError: Expected input batch_size (10016) to match target batch_size (22880).

In [23]:
print(inputs.shape)
print(output.shape)
print(labels.shape)

torch.Size([32, 313])
torch.Size([32, 313, 64834])
torch.Size([32, 715])


In [ ]:
print(output.shape)
print(labels.shape)

In [ ]:
loss_function(output.reshape(-1, output.size(-1)), doctor_answers.reshape(-1))